In [43]:
### The data is fetched from the raw FEC files. 

import ConfigParser
import psycopg2
import os
import csv
import sys

main_dir = os.getcwd()
data_dir = '../data/fec/'

# Connect to the database
def connect():
    # Read configurations from file
    config = ConfigParser.ConfigParser()
    config.read(main_dir + "/dbconfig.cnf")
    database = config.get('client', 'database')
    user = config.get('client', 'user')
    password = config.get('client', 'password')
    hostname = config.get('client', 'hostname')
    port = config.get('client', 'port')
    conn = psycopg2.connect(database=database, user = user, password = password, host = hostname, port = port)
    print "Opened database " + database
    return conn

# Read files:
def read_files(file_paths):
    lines = []
    for path in file_paths:
        f = open(path, 'r')
        new_lines = f.readlines()
        print "Length of new lines from path " + path + " " + str(len(new_lines))
        lines.extend(new_lines)
    return [line.split('|') for line in lines]

def read_data(paths, columns):
    raw = read_files(paths)
    data = [[row[column] for column in columns] for row in raw]
    return data

def read_csv_file(path):
    data = []
    with open(path) as csvfile:
        readCSV = csv.reader(csvfile, delimiter=',')
        for row in readCSV:
            data.append(row)
    return data

def write_csv_file(path, header_list, data):
    with open(path, 'wb') as csvfile:
        filewriter = csv.writer(csvfile)
        filewriter.writerow(header_list)
        for row in data:
            filewriter.writerow(row)

['C00371021', 'A', 'Q2', 'P', '27990778671', '15', 'IND', 'BEAL, ROBERT L.', 'BOSTON', 'MA', '02109', 'THE BEAL COMPANIES LLC', 'REAL ESTATE DEVELOPER', '05222007', '1000', '', 'C-23-01BH04', '307028', '', '', '4101520071081287609']


In [2]:
'''Committee To Committee Data'''

'''Create the Committee Committee Contribution'''
CMTE_TO_CMTE_CONTRIBUTED_ID_POS = 15
CMTE_TO_CMTE_CONTRIBUTOR_ID_POS = 0
CMTE_TO_CMTE_CONTRIBUTOR_NAME_POS = 7
CMTE_TO_CMTE_TRAN_DATE_POS = 13
CMTE_TO_CMTE_TRAN_AMOUNT_POS = 14
CMTE_TO_CMTE_TRAN_TYPE_POS = 5

committee_committee_paths = [(data_dir + 'pas2' + str(i)[2:] + '.txt') for i in range(1980, 2020, 2)]
committee_committee_data = read_files(committee_committee_paths)

Length of new lines from path ../data/fec/pas280.txt 132147
Length of new lines from path ../data/fec/pas282.txt 167410
Length of new lines from path ../data/fec/pas284.txt 198674
Length of new lines from path ../data/fec/pas286.txt 213355
Length of new lines from path ../data/fec/pas288.txt 214008
Length of new lines from path ../data/fec/pas290.txt 199434
Length of new lines from path ../data/fec/pas292.txt 228783
Length of new lines from path ../data/fec/pas294.txt 227032
Length of new lines from path ../data/fec/pas296.txt 250679
Length of new lines from path ../data/fec/pas298.txt 229613
Length of new lines from path ../data/fec/pas200.txt 247340
Length of new lines from path ../data/fec/pas202.txt 237106
Length of new lines from path ../data/fec/pas204.txt 245668
Length of new lines from path ../data/fec/pas206.txt 266703
Length of new lines from path ../data/fec/pas208.txt 305769
Length of new lines from path ../data/fec/pas210.txt 325095
Length of new lines from path ../data/fe

In [21]:
'''Committee Data'''

CMTE_ID_POS = 0
CMTE_NAME_POS = 1
CMTE_DSGN_POS = 8
CMTE_TP_POS = 9
CMTE_PTY_AFFILIATION_POS = 10
ORG_TP_POS = 12
CONNECTED_ORG_NAME_POS = 13

committee_paths = [(data_dir + 'cm' + str(i)[2:] + '.txt') for i in range(1980, 2020, 2)]
committee_data = read_files(committee_paths)

Length of new lines from path ../data/fec/cm80.txt 7884
Length of new lines from path ../data/fec/cm82.txt 8291
Length of new lines from path ../data/fec/cm84.txt 8465
Length of new lines from path ../data/fec/cm86.txt 8518
Length of new lines from path ../data/fec/cm88.txt 9218
Length of new lines from path ../data/fec/cm90.txt 9134
Length of new lines from path ../data/fec/cm92.txt 10759
Length of new lines from path ../data/fec/cm94.txt 10815
Length of new lines from path ../data/fec/cm96.txt 11075
Length of new lines from path ../data/fec/cm98.txt 9976
Length of new lines from path ../data/fec/cm00.txt 9577
Length of new lines from path ../data/fec/cm02.txt 9103
Length of new lines from path ../data/fec/cm04.txt 9322
Length of new lines from path ../data/fec/cm06.txt 9282
Length of new lines from path ../data/fec/cm08.txt 10017
Length of new lines from path ../data/fec/cm10.txt 11138
Length of new lines from path ../data/fec/cm12.txt 14455
Length of new lines from path ../data/fec/

In [47]:
### Find gvkeys of PACs, and create a table with PAC name, 
### PAC clean name, PAC id, gvkey, connected_org_name

pac_gvkey_path = '../data' + '/pac_1980_2014_gvkey_match.csv'
pac_gvkey_file = []
pac_gvkey_file_header = []

pac_gvkey_file = read_csv_file(pac_gvkey_path)
pac_gvkey_file_header = pac_gvkey_file[0]
pac_gvkey_file.pop(0)

['orig_name', 'clean_name', 'match_cos', 'gvkey', 'cos_score']

In [30]:
'''Create connected orgs'''

connected_orgs = {}
for row in committee_data:
    if row[CONNECTED_ORG_NAME_POS]:
        connected_orgs[row[CONNECTED_ORG_NAME_POS].lower()] = row

In [26]:
print connected_orgs.keys()[0:10]

['LATTA FOR CONGRESS', "PRESBYTERIAN MINISTERS' FUND", 'OCEAN FEDERAL SAVINGS BANK', 'TALECRIS BIOTHERAPEUTICS INC', 'CALIFORNIA LEAGUE OF FOOD PROCESSORS', 'ROHM & HASS CO', 'The PBSJ Corporation', "ALABAMA FEDERAL SAVINGS & LOAN ASS'N", 'GENERAL FINANCE CORP', 'MCDONALD HOPKINS LLC']


In [34]:
def find_corp_name(corporate_name):
    corporate_name = corporate_name.lower()
    if corporate_name in connected_orgs:
        row = connected_orgs[corporate_name]
        return True, row[CMTE_NAME_POS], row[CMTE_ID_POS], row[CONNECTED_ORG_NAME_POS]
    return False, '', '', ''

In [40]:
'''Find Committee IDs from Committee Names, Write To File'''
corp_pac_path = '../data' + '/corporate_pac.csv'
corp_pac_header = ['corporate_name', 'gvkey', 'pac_name', 'pac_id']
corp_pac_data = []

print 'pac_gvkey_file_length ', len(pac_gvkey_file)
for row in pac_gvkey_file: ## Very inefficient algorithm
    pac_gvkey_corporate_name = row[0]
    pac_corp_gvkey = row[3]
    cmte_exists, cmte_name, cmte_id, connected_org_name = find_corp_name(pac_gvkey_corporate_name)
    if cmte_exists:
        corp_pac_data.append([connected_org_name, pac_corp_gvkey, cmte_name, cmte_id])

print 'corp_pac_length ', len(corp_pac_data)

3274
3272
[['(DETROIT EDISON PAC) - (STATE)', '65089', 'DETROIT EDISON POLITICAL ACTION COMMITTEE - STATE', 'C00081547'], ['1-800 CONTACTS, INC.', '66425', '1-800 CONTACTS, INC. PAC', 'C00621912'], ['1ST SOURCE CORPORATION', '15199', '1ST SOURCE CORPORATION POLITICAL ACTION COMMITTEE', 'C00181529'], ['1ST SOURCE CORPORATION', '15199', '1ST SOURCE CORPORATION POLITICAL ACTION COMMITTEE', 'C00181529'], ['21ST CENTURY ONCOLOGY, INC', '265008', '21ST CENTURY ONCOLOGY, INC. POLITICAL ACTION COMMITTEE', 'C00385120'], ['21ST CENTURY PAC', '10771', 'MCKEON-21ST CENTURY PAC JOINT COMMITTEE', 'C00504308'], ['21ST CENTURY PARTY', '10771', "NATIONAL COMMITTEE OF THE 21ST CENTURY PARTY THE NATION'S EQUALITY PARTY", 'C00257659'], ['3COM CORPORATION', '10553', '3COM CORPORATION POLITICAL ACTION COMMITTEE', 'C00358614'], ['3M COMPANY', '7435', '3M COMPANY PAC', 'C00084475'], ['7-ELEVEN INC', '9872', '7 - ELEVEN INC PAC', 'C00549717']]


In [44]:
write_csv_file(corp_pac_path, corp_pac_header, corp_pac_data)

In [ ]:
'''Find Committee IDs from Committee Names, Write To File'''
corp_pac_path = 'data-matching' + '/corporate-pac.csv'
corp_pac_header = ['corporate_name', 'gvkey', 'pac_name', 'pac_id']

def create_corporate_table(paths):

    committee = read_csv_file(paths)

    # Connect to the database
    conn = connect()
    cur = conn.cursor()

    cur.execute("DROP TABLE IF EXISTS CORPORATE;")
    cur.execute('''CREATE TABLE CORPORATE
          (CORPORATE_NAME       CHAR(200),              NOT NULL,
          GVKEY                 NUMERIC(14,2)           NOT NULL,
          COMMITTEE_NAME        CHAR(200)               NOT NULL,
          COMMITTEE_ID          CHAR(9)                 NOT NULL);''')
    print "Table created successfully"

    for path in paths:
        # election_cycle = path[len(path)-6:len(path)-4] # Assuming the path ends in format like ../indiv90.txt
        conn = connect()
        cur = conn.cursor()

        print "Files are read from ", path
        raw_lines = read_raw_lines([path])

        for i in range(len(raw_lines)):
            line_raw = raw_lines[i]
            row = line_raw.split("|")
            row = [elem.strip() for elem in row]

            query = "INSERT INTO COMMITTEE (CORPORATE_NAME,GVKEY,COMMITTEE_NAME,COMMITTEE_ID) \
                VALUES (%s, %s, %s, %s)"
            cur.execute(query, row)

    conn.commit()
    conn.close()
    print "Corporate table is created successfully"

In [10]:
create_corporate_table(corp_pac_path):

ImportError: No module named fuzzywuzzy

In [ ]:
'''Create Employer Table with employer_name, clean_name, gvkey'''
employer_path = '../data' + '/employer.csv'
employer_header = ['employer_name', 'gvkey', 'clean_name']
employer_data = []

def create_employer_table(paths):

    committee = read_csv_file(paths)

    # Connect to the database
    conn = connect()
    cur = conn.cursor()

    cur.execute("DROP TABLE IF EXISTS EMPLOYER;")
    cur.execute('''CREATE TABLE CORPORATE
          (EMPLOYER_NAME        CHAR(200),              NOT NULL,
          CLEAN_NAME            CHAR(200),              NOT NULL,
          GVKEY                 NUMERIC(14,2)           NOT NULL);''')
    print "Table created successfully"

    for path in paths:
        # election_cycle = path[len(path)-6:len(path)-4] # Assuming the path ends in format like ../indiv90.txt
        conn = connect()
        cur = conn.cursor()

        print "Files are read from ", path
        raw_lines = read_raw_lines([path])

        for i in range(len(raw_lines)):
            line_raw = raw_lines[i]
            row = line_raw.split("|")
            row = [elem.strip() for elem in row]

            query = "INSERT INTO COMMITTEE (CORPORATE_NAME,GVKEY,COMMITTEE_NAME,COMMITTEE_ID) \
                VALUES (%s, %s, %s, %s)"
            cur.execute(query, row)

    conn.commit()
    conn.close()
    print "Corporate table is created successfully"

In [115]:
csv.field_size_limit(sys.maxsize)

def read_csv_file(path):
    data = []
    with open(path) as csvfile:
        readCSV = csv.reader(csvfile, delimiter=',')
        for row in readCSV:
            data.append(row)
    return data

# def read_csv_file(path):
#     with open(path) as csvfile:
#         lines = csvfile.readlines()
#     return lines
# #         readCSV = csv.reader(csvfile, delimiter=',')
# # #         lines = readCSV.readlines()
# #         print sum(1 for line in readCSV)
# #         for row in itertools.islice(readCSV, 0, 50):
# #             data.append(row)
# #     return data

employer_path = '../data' + '/empl_1980_2014_gvkey_match.csv'
data = read_csv_file(employer_path)
print len(data)
print data
# print data[0:10]
# print data[3]
# print data[3].rstrip('\'\"\r\n')
# # print [[elem.rstrip('\'\"\r\n') for elem in row] for row in data[3]]
# print [elem.rstrip('\'\"\r\n') for elem in data[3]]
# print len(data)

98169
[['orig_name', 'clean_name', 'match_cos', 'gvkey', 'cos_score'], ["'''RED HAT INC.'''", 'red hat inc', 'RED HAT INC', '122841', '100'], ["''ANN'' COMPANY", 'ann co', 'ANN INC', '21828', '82.531845992'], ["' PROPERTIES", 'properties', 'BRE PROPERTIES INC', '2025', '82.5327151753'], ["'8X8 INC.'", '8x8 inc', '8X8 INC', '65021', '100'], ["'ADSTAR INC.'", 'adstar inc', 'ADSTAR INC', '124934', '100'], ["'AME COMMUNITY SERVICES INC.'", 'ame community services inc', 'AMERICAN COMMUNITY SERVICES', '1423', '82.3940337528'], ["'ANN CO.", 'ann co', 'ANN INC', '21828', '82.531845992'], ["'APOLLO GROUP, INC..'", 'apollo group inc', 'APOLLO EYE GROUP INC', '29691', '84.7912010613'], ["'APPLIX INC'", 'applix inc', 'APPLIX INC', '31144', '100'], ["'ASSURANT INC.'", 'assurant inc', 'ASSURANT INC', '157057', '100'], ["'AUTODESK INC.'", 'autodesk inc', 'AUTODESK INC', '1878', '100'], ["'CAR INC.'", 'car inc', 'CAR INC', '170614', '100'], ["'CATALYTICA ENERGY SYSTEMS INC.'", 'catalytica energy syste